In [ ]:
%pip install langchain_community docx2txt langchain_chroma langchainhub

In [1]:
from langchain_community.document_loaders import Docx2txtLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter

text_splitter = RecursiveCharacterTextSplitter(
    chunk_size=800,
    chunk_overlap=100,
)

# 개인정보 보호법
document_name = './privacy_with_markdown.docx'

loader = Docx2txtLoader(document_name)
document_list = loader.load_and_split(text_splitter=text_splitter)

In [2]:
len(document_list)

111

In [3]:
from dotenv import load_dotenv
from langchain_openai import OpenAIEmbeddings

# 환경변수를 불러옴
load_dotenv()

# OpenAI에서 제공하는 Embedding Model을 활용해서 `chunk`를 vector화
embedding = OpenAIEmbeddings(model='text-embedding-3-large')
texts = [d.page_content for d in document_list]
vectors = embedding.embed_documents(texts)

In [4]:
texts

['개인정보 보호법\n\n개인정보 보호법\n\n[시행 2024. 3. 15.] [법률 제19234호, 2023. 3. 14., 일부개정]\n\n개인정보보호위원회(심사총괄담당관 - 일반 법령해석) 02-2100-3043\n\n개인정보보호위원회(국제협력담당관 - 국외이전) 02-2100-2484, 2499\n\n개인정보보호위원회(개인정보보호정책과 - 법령 제ㆍ개정, 아동ㆍ청소년) 02-2100-3057, 3047\n\n개인정보보호위원회(신기술개인정보과 - 영상정보, 안전조치) 02-2100-3064, 3028\n\n개인정보보호위원회(데이터안전정책과 - 가명정보, 개인정보안심구역) 02-2100-3088, 3074, 3058, 3079\n\n개인정보보호위원회(자율보호정책과 - 보호책임자, 자율규제, 보호수준 평가, 처리방침, 영향평가) 02-2100-3083, 3089, 3087, 3096, 3086\n\n개인정보보호위원회(분쟁조정과 - 분쟁조정, 손해배상책임) 1833-6972, 02-2100-3142\n\n개인정보보호위원회(범정부마이데이터 추진단(전략기획팀 - 전송요구권(마이데이터)) 02-2100-3173\n\n\n\n제1장 총칙\n\n\n\n제1조(목적) 이 법은 개인정보의 처리 및 보호에 관한 사항을 정함으로써 개인의 자유와 권리를 보호하고, 나아가 개인의 존엄과 가치를 구현함을 목적으로 한다. <개정 2014. 3. 24.>\n\n\n\n제2조(정의) 이 법에서 사용하는 용어의 뜻은 다음과 같다. <개정 2014. 3. 24., 2020. 2. 4., 2023. 3. 14.>',
 '제2조(정의) 이 법에서 사용하는 용어의 뜻은 다음과 같다. <개정 2014. 3. 24., 2020. 2. 4., 2023. 3. 14.>\n\n1. “개인정보”란 살아 있는 개인에 관한 정보로서 다음 각 목의 어느 하나에 해당하는 정보를 말한다.\n\n가. 성명, 주민등록번호 및 영상 등을 통하여 개인을 알아볼 수 있는 정보\n\n나. 해당 정보만으로는 특정 개인을 알아볼

In [5]:
vectors

[[-0.024258457124233246,
  -0.04049871489405632,
  0.004170483909547329,
  0.020758988335728645,
  0.02752009965479374,
  -0.005167096853256226,
  0.0029728501103818417,
  0.02496061660349369,
  -0.006200516130775213,
  -0.00761049659922719,
  0.032661713659763336,
  -0.003601395757868886,
  0.020736338570713997,
  0.00443662516772747,
  0.01580990105867386,
  -0.023850752040743828,
  -0.03798453137278557,
  -0.014881238341331482,
  0.006200516130775213,
  -0.015504121780395508,
  0.02253703586757183,
  -0.006953638046979904,
  0.014269680716097355,
  0.04568563029170036,
  0.005113302264362574,
  0.018358057364821434,
  0.03125739470124245,
  -0.0033635676372796297,
  0.04135942459106445,
  -0.0011643663747236133,
  0.03485879302024841,
  0.026432884857058525,
  0.013692098669707775,
  0.0052520353347063065,
  0.013975227251648903,
  -0.012253805063664913,
  0.0038335612043738365,
  0.0325031615793705,
  -0.005696547217667103,
  -0.010611659847199917,
  -0.011251529678702354,
  0.0090

In [21]:
import os

# Connect using a MilvusClient object
from pymilvus import MilvusClient, DataType

milvus_end_point = os.getenv('MILVUS_CLUSTER_ENDPOINT')
milvus_token = os.getenv('MILVUS_TOKEN')

# 1. Set up a Milvus client
client = MilvusClient(
    uri=milvus_end_point,
    token=milvus_token
)

In [22]:
import time

# 개인정보 보호법
collection_name = 'privacy_collection'
vector_dimension = 3072
document_max_length = 2000

# 2. Create a collection in customized setup mode

# 2.1 Create schema
schema = MilvusClient.create_schema(
    auto_id=False,
    enable_dynamic_field=True
)

# 2.2 Add fields to schema
schema.add_field(field_name="id", datatype=DataType.INT64, is_primary=True)
schema.add_field(field_name="vector", datatype=DataType.FLOAT_VECTOR, dim=vector_dimension)
schema.add_field(field_name="document", datatype=DataType.VARCHAR, max_length=document_max_length)

# 2.3 Prepare index parameters
index_params = client.prepare_index_params()

# 2.4 Add index
index_params.add_index(
    field_name="id",
    index_type="STL_SORT"
)

index_params.add_index(
    field_name="vector",
    index_type="AUTOINDEX",
    metric_type="IP",
    index_name="privacy_vector_index"
)

index_params.add_index(
    field_name="document",
    index_type="AUTOINDEX",
    index_name="privacy_document_index"
)

collection_name = 'privacy_collection'
res = client.get_load_state(
    collection_name=collection_name
)
print(f"{collection_name} state: {res['state']}")
res_state = str(res['state'])

# 2.5 Create a collection with the index loaded simultaneously
is_create = False
if res_state == 'NotExist':
    is_create = True
print(f"is_create: {is_create}")

if is_create:
    print(f"Create collection: {collection_name}")

    client.create_collection(
        collection_name=collection_name,
        schema=schema,
        index_params=index_params
    )

    time.sleep(5)

    res = client.get_load_state(
        collection_name=collection_name
    )

privacy_collection state: Loaded
is_create: False


In [8]:
# Generate dataset
data = []
# max_vector = 0
# max_document = 0

for i in range(len(vectors)):
    item = {
        "id": i,
        "vector": vectors[i],
        "document": texts[i]
    }
    data.append(item)

    # if len(vectors[i]) > max_vector:
    #     max_vector = len(vectors[i])
    # if len(texts[i]) > max_document:
    #     max_document = len(texts[i])

len(data)

111

In [67]:
# 3. Insert data
res = client.upsert(
    collection_name=collection_name,
    data=data
)

print(res)

{'upsert_count': 111, 'cost': 0}


In [ ]:
%pip install sentence_transformers

In [23]:
import torch

from torch import nn
from sentence_transformers import SentenceTransformer

# Embedding
# model_name = 'openai-gpt'
# model_name = 'paraphrase-MiniLM-L6-v2'  # 384
model_name = 'klue/bert-base'  # 768
model = SentenceTransformer(model_name)

# 벡터 차원 조정
class DimensionAdjuster(nn.Module):
    def __init__(self, input_dim, output_dim):
        super(DimensionAdjuster, self).__init__()
        self.fc = nn.Linear(input_dim, output_dim)
    
    def forward(self, x):
        return self.fc(x)
    
# 모델 차원 초기화
input_dim = 768
output_dim = 3072
dimension_adjuster = DimensionAdjuster(input_dim, output_dim)

# Create search query
# 개인정보 보호법
query_texts = ['개인정보 유출 시 대응 방법은 무엇인가요?']
query_embeddings = model.encode(query_texts)
print(f"모델 벡터 차원: {len(query_embeddings)}")

# 벡터 차원 조정
query_embeddings_tensor = torch.tensor(query_embeddings)
adjusted_embeddings = dimension_adjuster(query_embeddings_tensor).tolist()
print("조정된 벡터 차원:", len(adjusted_embeddings[0]))

n_results = 3

# Define the fields to retrieve in the search results
fields_to_retrieve = ["id", "vector", "document"]

# Search
results = client.search(
    collection_name=collection_name,
    data=adjusted_embeddings,
    anns_field="vector",
    limit=n_results,
    fields=fields_to_retrieve
)

for result in results:
    print(result)

No sentence-transformers model found with name klue/bert-base. Creating a new one with mean pooling.


모델 벡터 차원: 1
조정된 벡터 차원: 3072
[{'id': 98, 'distance': 1.1271885633468628, 'entity': {}}, {'id': 41, 'distance': 1.0508267879486084, 'entity': {}}, {'id': 102, 'distance': 1.04183828830719, 'entity': {}}]


In [24]:
id_list = []
distance_list = []

for result in results:
    print(result)

    id_list = [item['id'] for item in result]
    distance_list = [item['distance'] for item in result]

id_list
# distance_list

[{'id': 98, 'distance': 1.1271885633468628, 'entity': {}}, {'id': 41, 'distance': 1.0508267879486084, 'entity': {}}, {'id': 102, 'distance': 1.04183828830719, 'entity': {}}]


[98, 41, 102]

In [25]:
# document 조회
def fetch_data_by_ids(ids):
    fields = ['id', 'document']
    results = client.get(
        collection_name=collection_name,
        ids=ids,
        output_fields=fields
    )
    
    return results

retrieved_docs = []
for index in range(len(id_list)):
    documents = fetch_data_by_ids(id_list[index])

    for document in documents:
        # print(document)
        retrieved_docs.append(document['document'])

retrieved_docs

['2. 제18조제1항ㆍ제2항, 제27조제3항 또는 제28조의2(제26조제8항에 따라 준용되는 경우를 포함한다), 제19조 또는 제26조제5항을 위반하여 개인정보를 이용하거나 제3자에게 제공한 자 및 그 사정을 알면서도 영리 또는 부정한 목적으로 개인정보를 제공받은 자\n\n3. 제22조의2제1항(제26조제8항에 따라 준용되는 경우를 포함한다)을 위반하여 법정대리인의 동의를 받지 아니하고 만 14세 미만인 아동의 개인정보를 처리한 자\n\n4. 제23조제1항(제26조제8항에 따라 준용되는 경우를 포함한다)을 위반하여 민감정보를 처리한 자\n\n5. 제24조제1항(제26조제8항에 따라 준용되는 경우를 포함한다)을 위반하여 고유식별정보를 처리한 자\n\n6. 제28조의3제1항(제26조제8항에 따라 준용되는 경우를 포함한다)을 위반하여 보호위원회 또는 관계 중앙행정기관의 장으로부터 전문기관으로 지정받지 아니하고 가명정보를 결합한 자\n\n7. 제28조의3제2항(제26조제8항에 따라 준용되는 경우를 포함한다)을 위반하여 전문기관의 장의 승인을 받지 아니하고 결합을 수행한 기관 외부로 결합된 정보를 반출하거나 이를 제3자에게 제공한 자 및 그 사정을 알면서도 영리 또는 부정한 목적으로 결합된 정보를 제공받은 자\n\n8. 제28조의5제1항(제26조제8항에 따라 준용되는 경우를 포함한다)을 위반하여 특정 개인을 알아보기 위한 목적으로 가명정보를 처리한 자\n\n9. 제59조제2호를 위반하여 업무상 알게 된 개인정보를 누설하거나 권한 없이 다른 사람이 이용하도록 제공한 자 및 그 사정을 알면서도 영리 또는 부정한 목적으로 개인정보를 제공받은 자',
 '② 개인정보처리자는 제1항제1호에 따른 동의를 받을 때에는 미리 다음 각 호의 사항을 정보주체에게 알려야 한다.\n\n1. 이전되는 개인정보 항목\n\n2. 개인정보가 이전되는 국가, 시기 및 방법\n\n3. 개인정보를 이전받는 자의 성명(법인인 경우에는 그 명칭과 연락처를 말한다)\n\n4. 개인정보를 이전받는 자의 개인정

In [26]:
from openai import OpenAI
client = OpenAI()

# 개인정보 보호법
law_content = f"당신은 한국의 개인정보 보호법 전문가 입니다. 아래 내용을 참고해서 사용자의 질문에 답변해주세요 {retrieved_docs}"
query = '개인정보 유출 시 대응 방법은 무엇인가요?'

response = client.chat.completions.create(
  model="gpt-4o",
  messages=[
    {"role": "system", "content": law_content},
    {"role": "user", "content": query}
  ]
)

In [27]:
response.choices[0].message.content

'개인정보 유출 시에는 신속하고 체계적인 대응이 필요합니다. 한국의 개인정보 보호법에 따라 개인정보 유출 시 취해야 할 주요 대응 방법은 다음과 같습니다:\n\n1. **즉각적인 조치**\n   - **유출 경위 파악**: 유출된 개인정보 항목, 유출 시점 및 발생 경위 등을 신속하게 파악합니다.\n   - **추가 유출 방지**: 개인정보 유출이 확산되지 않도록 시스템 점검 및 필요한 보호 조치를 즉시 시행합니다.\n   \n2. **내부 보고 및 외부 통지**\n   - **내부 보고**: 조직 내 책임자 및 관련 부서에 신속하게 보고합니다.\n   - **정보주체 통지**: 유출된 개인정보의 영향을 받을 수 있는 정보주체들에게 유출 사실, 내용, 피해 최소화를 위한 조치 방안 등을 지체 없이 통지합니다.\n   - **보호위원회 신고**: 개인정보 보호위원회에 일정 기준 이상의 개인정보 유출이 발생한 경우 지체 없이 유출 사실을 신고해야 합니다.\n\n3. **후속 조치**\n   - **피해 최소화 조치**: 피해를 최소화하기 위한 조치를 강구하고, 필요 시 정보주체에 대한 지원 방안을 마련합니다.\n   - **재발 방지 대책 수립**: 유출 원인 분석을 통해 재발 방지 대책을 수립하고 측정합니다.\n   \n4. **공식적인 절차 준수**\n   - 개인정보 보호법 및 관련 법령에 따라 공식적인 절차 및 지침을 준수합니다.\n\n구체적으로 개인정보 보호법 제34조에 따르면, 개인정보처리자는 개인정보가 유출된 경우 다음과 같은 내용을 정보주체에게 알려야 합니다:\n\n1. 유출된 개인정보 항목\n2. 유출된 시점과 경위\n3. 유출로 인한 피해를 최소화하기 위해 정보주체가 할 수 있는 방법\n4. 개인정보처리자가 대응하고 있는 상황\n5. 정보주체가 상담을 접수할 수 있는 부서 및 관련 연락처\n\n마지막으로, 개인정보 보호위원회에 신고할 때는 다음의 사항을 포함해야 합니다:\n\n1. 유출된 개인정보의 항목\n2. 유출된 시점과 경위\n3. 유출로 